this file prepares info of genes and works out a dataframe

	ChIP-seq signals
	cRAM distri (shared or specific cRAM)
	DEG
	pathways intersect 
	in which Episig section
	if literature support
	which TF's regulatee, if weight-changed regulatees



In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import seaborn as sns
import matplotlib
import os, sys

In [2]:
tf_dt = pd.read_csv('/stg3/data3/peiyao/work/20230922.Lina_lung/results/taiji/TF_MWU.txt')
tf_dt.iloc[:3, ]


Unnamed: 0          TF      pval  mean_cancer  mean_normal  fold_change  \
0           1  AC023509.3  0.149378     0.000009     0.000011     0.854486   
1           2  AC138696.1  0.054814     0.000013     0.000015     0.879914   
2           3         AHR  0.098957     0.000295     0.000224     1.317981   

     log2FC  pval.adjust  
0 -0.226872     0.552460  
1 -0.184566     0.469544  
2  0.398330     0.499067

In [4]:
tf_dt_ = tf_dt[tf_dt['pval']<=0.05]
print(len(tf_dt_))
tf_dt_.iloc[:3, ]

118


Unnamed: 0      TF      pval  mean_cancer  mean_normal  fold_change  \
6            7    ALX4  0.015922     0.000093     0.000067     1.385575   
9           10   ARGFX  0.011224     0.000045     0.000053     0.842539   
10          11  ARID3A  0.000499     0.000623     0.000956     0.651917   

      log2FC  pval.adjust  
6   0.470485     0.394657  
9  -0.247184     0.373602  
10 -0.617239     0.351448

In [5]:
# save two files: full_info + concise_info
tf_dt_ = tf_dt_[['TF', 'fold_change', 'log2FC']].copy()
tf_dt_.columns = ['gene', 'FC_PR_of_TF', 'log2FC_PR_of_TF']
tf_dt_.iloc[:3, ]


gene  FC_PR_of_TF  log2FC_PR_of_TF
6     ALX4     1.385575         0.470485
9    ARGFX     0.842539        -0.247184
10  ARID3A     0.651917        -0.617239

In [7]:
tf_dt_['type'] = 'sig_TF'

In [9]:
tf_dt_.to_csv(os.path.join(
    '/stg3/data3/peiyao/work/20230922.Lina_lung/results/20231223.final_integrate/00.gene_info',
    'gene_list.sig_TF.txt'
    ), sep='\t', index=None, )

In [34]:
# now, check all DEGs

deg_dt = pd.read_csv(os.path.join(
    '/stg3/data3/peiyao/work/20230922.Lina_lung/data/DESEQ',
    'all.gene.samples.deseq2.results.new2022.txt'
), sep='\t', )
deg_dt.iloc[:3, ]



baseMean  log2FoldChange     lfcSE      stat    pvalue      padj
5S_rRNA   0.339105        0.639426  1.031768  0.619739  0.535430       NaN
7SK      16.639565       -0.030040  0.206296 -0.145616  0.884224  0.962589
A1BG     69.380497       -0.421846  0.216114 -1.951962  0.050943  0.269818

In [35]:
deg_dt.reset_index(inplace=True, )
deg_dt['padj'].fillna(1, inplace=True, )
deg_dt.iloc[:3, ]

index   baseMean  log2FoldChange     lfcSE      stat    pvalue      padj
0  5S_rRNA   0.339105        0.639426  1.031768  0.619739  0.535430  1.000000
1      7SK  16.639565       -0.030040  0.206296 -0.145616  0.884224  0.962589
2     A1BG  69.380497       -0.421846  0.216114 -1.951962  0.050943  0.269818

In [36]:
deg_dt_ = deg_dt[(deg_dt['padj']<=0.0001) &
                (
                    (deg_dt['log2FoldChange']<=-1) | (deg_dt['log2FoldChange']>=1)
                )].copy()
print(len(deg_dt_))
deg_dt_.iloc[:3, ]

96


index   baseMean  log2FoldChange     lfcSE      stat        pvalue  \
48         ABCA4  83.208249       -2.334132  0.436651 -5.345536  9.015003e-08   
58         ABCB4  21.807304       -2.301652  0.433768 -5.306185  1.119434e-07   
1798  AC105206.1  25.516768        3.925662  0.505173  7.770926  7.791465e-15   

              padj  
48    4.011273e-05  
58    4.571586e-05  
1798  7.742639e-11

In [37]:
deg_dt__ = deg_dt_[['index', 'log2FoldChange']].copy()
deg_dt__.columns = ['gene','log2FC_DEG']
deg_dt__['type'] = 'DEG_norm_vs_can'

In [39]:
deg_dt__.iloc[:3, ]

gene  log2FC_DEG             type
48         ABCA4   -2.334132  DEG_norm_vs_can
58         ABCB4   -2.301652  DEG_norm_vs_can
1798  AC105206.1    3.925662  DEG_norm_vs_can

In [40]:
deg_dt__.to_csv(os.path.join(
    '/stg3/data3/peiyao/work/20230922.Lina_lung/results/20231223.final_integrate/00.gene_info',
    'gene_list.DEG.txt'
), sep='\t', index=None, )

In [3]:
# prep regulatees
dt_folder = '/stg3/data3/peiyao/work/20230922.Lina_lung/results/taiji/edges.2.20231019'
edge_dt_1 = pd.read_csv(os.path.join(
    dt_folder,
    'regulatee_list.pval_sig.txt'), sep='\t', )
edge_dt_2 = pd.read_csv(os.path.join(
    dt_folder,
    'regulatee_list.pval_sig.new_sig_TF.txt'), sep='\t', )
edge_dt_3 = pd.read_csv(os.path.join(
    dt_folder,
    'regulatee_list.pval_sig.new_new_sig_TF.txt'), sep='\t', )    

edge_dt = pd.concat((edge_dt_1, edge_dt_2, edge_dt_3), ignore_index=True, )


edge_dt.iloc[:3, ]


start     end specificity      diff      pval  exist_in_cancer  \
0  ARID3A   ABCD2      normal -0.349036  0.000000                0   
1  ARID3A   ABCG2      normal -0.189381  0.000000                0   
2  ARID3A  ABHD12      shared -0.145894  0.043782               14   

   mean_cancer  std_cancer  exist_in_normal  mean_normal  std_normal  
0     0.000000    0.000000                6     0.349036    0.302465  
1     0.000000    0.000000                5     0.189381    0.120483  
2     0.233115    0.149052               16     0.379009    0.242060

In [10]:
edge_dt_ = edge_dt[['start', 'end', 'diff']].copy()
len(edge_dt_)

23985

In [7]:
len(set(list(edge_dt_['start']))) # 42 top TFs

42

In [11]:
for i_, (TF, edge_dt__) in enumerate(edge_dt_.groupby('start')):
    # print(TF, edge_dt__)
    edge_dt__sorted = edge_dt__.copy().sort_values('diff', ascending=False, )
    N = len(edge_dt__sorted)
    top_N = min(N, 200)
    if i_==0:
        result_df = edge_dt__sorted.iloc[:top_N, ].copy()
    else:
        result_df = pd.concat((result_df, edge_dt__sorted.iloc[:top_N, ].copy()), ignore_index=True, )

result_df

start           end      diff
0     ARID3A          SOX4  0.230728
1     ARID3A         Y_RNA -0.044912
2     ARID3A      IPO9-AS1 -0.078878
3     ARID3A        DCAF13 -0.083899
4     ARID3A        SNOU13 -0.084553
...      ...           ...       ...
5680  ZNF610         EXOC2 -0.105876
5681  ZNF610  RP11-532F6.3 -0.105876
5682  ZNF610  RP11-532F6.4 -0.105876
5683  ZNF610          ZNF7 -0.115612
5684  ZNF610        DUSP22 -0.132494

[5685 rows x 3 columns]

In [12]:
result_df.columns = ['TF_start', 'gene', 'regulatee_diff']
result_df[['gene', 'TF_start', 'regulatee_diff']].to_csv(os.path.join(
    '/stg3/data3/peiyao/work/20230922.Lina_lung/results/20231223.final_integrate/00.gene_info',
    'gene_list.sig_regulatees.txt'
), sep='\t', index=None, )



In [2]:
# find overlap genes and derive these gene;s coordinates including promoter loc and gene body loc

g1 = pd.read_csv('/stg3/data3/peiyao/work/20230922.Lina_lung/results/20231223.final_integrate/00.gene_info/gene_list.DEG.txt', sep='\t', )
g2 = pd.read_csv('/stg3/data3/peiyao/work/20230922.Lina_lung/results/20231223.final_integrate/00.gene_info/gene_list.sig_TF.txt', sep='\t', )
g3 = pd.read_csv('/stg3/data3/peiyao/work/20230922.Lina_lung/results/20231223.final_integrate/00.gene_info/gene_list.sig_regulatees.txt', sep='\t', )

print(g1.iloc[:3, ])
print(g2.iloc[:3, ])
print(g3.iloc[:3, ])



         gene  log2FC_DEG             type
0       ABCA4   -2.334132  DEG_norm_vs_can
1       ABCB4   -2.301652  DEG_norm_vs_can
2  AC105206.1    3.925662  DEG_norm_vs_can
     gene  FC_PR_of_TF  log2FC_PR_of_TF    type
0    ALX4     1.385575         0.470485  sig_TF
1   ARGFX     0.842539        -0.247184  sig_TF
2  ARID3A     0.651917        -0.617239  sig_TF
       gene TF_start  regulatee_diff
0      SOX4   ARID3A        0.230728
1     Y_RNA   ARID3A       -0.044912
2  IPO9-AS1   ARID3A       -0.078878


In [3]:
S = set(list(g1['gene']) + list(g2['gene']) + list(g3['gene']))
len(S)

4923

In [4]:
# add prom loc and gene body loc to gene list, prep a bed file

gencode = pd.read_csv('/stg3/data3/peiyao/data/gencode/gencode.v19.annotation.gtf', sep='\t', skiprows=5, header=None, ) 
gencode = gencode[gencode[2]=='transcript'].copy().reset_index(drop=True)

gname_list = []
for i in list(gencode[8]):
    i_ = i.split('; ')
    for i__ in i_:
        if len(i__)>10:
            if i__[:9]=='gene_name':
                gname_list.append(i__.split('"')[1])

gencode['gene_name'] = gname_list
gencode = gencode[[0,3,4,6,'gene_name']]
gencode.columns = ['chr','s','e','strand','gene_name']
gencode = gencode[gencode['chr']!='chrM']

gencode.iloc[:3, ]


chr      s      e strand gene_name
0  chr1  11869  14409      +   DDX11L1
1  chr1  11872  14412      +   DDX11L1
2  chr1  11874  14409      +   DDX11L1

In [5]:
# merge dt
dt = pd.DataFrame({'gene':list(S)})
print(dt.iloc[:3, ])
# dt.reset_index(inplace=True, )

dt = dt.merge(gencode, how='inner', left_on='gene', right_on='gene_name')

dt['s'] = dt['s'].astype(int) 
dt['e'] = dt['e'].astype(int) 

print(dt.iloc[:3, ])

            gene
0         NECAB3
1          AKTIP
2  RP11-276E17.2
     gene    chr         s         e strand gene_name
0  NECAB3  chr20  32244893  32247353      -    NECAB3
1  NECAB3  chr20  32244893  32262214      -    NECAB3
2  NECAB3  chr20  32244893  32262269      -    NECAB3


In [6]:
# find promoter loc at different thresh
ups_len = 1000
downs_len = 0

# for pos or neg strand
dt_sub_pos = dt[dt['strand']=='+'].copy()
dt_sub_pos['promoter_coord1'] = dt_sub_pos['s']-ups_len
dt_sub_pos['promoter_coord2'] = dt_sub_pos['s']+downs_len

dt_sub_neg = dt[dt['strand']=='-'].copy()
dt_sub_neg['promoter_coord1'] = dt_sub_neg['e']-downs_len
dt_sub_neg['promoter_coord2'] = dt_sub_neg['e']+ups_len

dt_sub = pd.concat((dt_sub_pos, dt_sub_neg), ignore_index=True, )
print(dt_sub.iloc[:3, ])

    gene    chr         s         e strand gene_name  promoter_coord1  \
0  HOXC4  chr12  54410715  54449111      +     HOXC4         54409715   
1  HOXC4  chr12  54431638  54447208      +     HOXC4         54430638   
2  HOXC4  chr12  54447661  54449813      +     HOXC4         54446661   

   promoter_coord2  
0         54410715  
1         54431638  
2         54447661  


In [7]:
len(set(list(dt_sub['gene']))) # 4829

4829

In [11]:
# prepare a bed file
for i, (g_, dt_) in enumerate(dt_sub.groupby('gene')):
    dt_['txn_idx_gene_body'] = dt_['gene'] +['__body__{}'.format(i_) for i_ in range(len(dt_))]
    dt_['txn_idx_promoter'] = dt_['gene'] +['__prom__{}'.format(i_) for i_ in range(len(dt_))]
    # print(dt_)
    gb_dt_cur = dt_[['chr','s','e','txn_idx_gene_body']].copy()
    pr_dt_cur = dt_[['chr','promoter_coord1','promoter_coord2','txn_idx_promoter']].copy()
    
    gb_dt_cur.columns = ['c','s','e','n']
    pr_dt_cur.columns = ['c','s','e','n']

    bed_result_current = pd.concat((
        gb_dt_cur,
        pr_dt_cur
        ), ignore_index=True, )

    if i==0:
        bed_result = bed_result_current.copy()
    else:
        bed_result = pd.concat((bed_result, bed_result_current), ignore_index=True, )
    
bed_result.iloc[:30, ]     

    


      gene    chr          s          e strand gene_name  promoter_coord1  \
9568   7SK   chr6  136866330  136866630      +       7SK        136865330   
9569   7SK   chr8  144624280  144624570      +       7SK        144623280   
9570   7SK   chr8  144624280  144624568      +       7SK        144623280   
9571   7SK  chr13   45697228   45697549      +       7SK         45696228   
9572   7SK  chr16   81993524   81996298      +       7SK         81992524   
9573   7SK  chr16   81995531   81995848      +       7SK         81994531   
9574   7SK  chr21   26467335   26475983      +       7SK         26466335   
9575   7SK  chr21   26467355   26475983      +       7SK         26466355   
9576   7SK  chr21   26473445   26473728      +       7SK         26472445   
27744  7SK   chr5   68266266   68266579      -       7SK         68266579   
27745  7SK   chr5   68266519   68325754      -       7SK         68325754   
27746  7SK   chr5   68322582   68325992      -       7SK         68325992   

c          s          e                 n
0    chr6  136866330  136866630      7SK__body__0
1    chr8  144624280  144624570      7SK__body__1
2    chr8  144624280  144624568      7SK__body__2
3   chr13   45697228   45697549      7SK__body__3
4   chr16   81993524   81996298      7SK__body__4
5   chr16   81995531   81995848      7SK__body__5
6   chr21   26467335   26475983      7SK__body__6
7   chr21   26467355   26475983      7SK__body__7
8   chr21   26473445   26473728      7SK__body__8
9    chr5   68266266   68266579      7SK__body__9
10   chr5   68266519   68325754     7SK__body__10
11   chr5   68322582   68325992     7SK__body__11
12   chrX   12632122   12632316     7SK__body__12
13   chr6  136865330  136866330      7SK__prom__0
14   chr8  144623280  144624280      7SK__prom__1
15   chr8  144623280  144624280      7SK__prom__2
16  chr13   45696228   45697228      7SK__prom__3
17  chr16   81992524   81993524      7SK__prom__4
18  chr16   81994531   81995531      7SK__prom__5
19  chr21   26466335   26467335      7SK__prom__6
20  chr21   26466355   26467355      7SK__prom__7
21  chr21   26472445   26473445      7SK__prom__8
22   chr5   68266579   68267579      7SK__prom__9
23   chr5   68325754   68326754     7SK__prom__10
24   chr5   68325992   68326992     7SK__prom__11
25   chrX   12632316   12633316     7SK__prom__12
26  chr12    9217773    9220651  A2M-AS1__body__0
27  chr12    9216773    9217773  A2M-AS1__prom__0
28  chr12   53701240   53715415     AAAS__body__0
29  chr12   53701241   53715041     AAAS__body__1

In [ ]:
bed_result.to_csv(os.path.join(
    '/stg3/data3/peiyao/work/20230922.Lina_lung/results/20231223.final_integrate/01.gene_prom_body_loc.bed',
    'all_genes.hg19.bed'
), sep='\t', index=None, header=None, )